In [1]:
import re
import sys
from nltk.corpus import stopwords
import nltk
import pandas as pd
import numpy as np
from sklearn.feature_extraction import text
from sklearn.feature_extraction.text import CountVectorizer
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Embedding, LSTM, SpatialDropout1D
from sklearn.model_selection import train_test_split
from keras.utils.np_utils import to_categorical
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

Using TensorFlow backend.


In [2]:
data=pd.read_csv('Data.csv')

In [3]:
data.head()

id                                title  \
0   1                Doctor Assisted Dying   
1   2  Local Government Finance (Scotland)   
2   2  Local Government Finance (Scotland)   
3   2  Local Government Finance (Scotland)   
4   2  Local Government Finance (Scotland)   

                                              motion  manual_motion  \
0  That leave be given to bring in a Bill to enab...              1   
1  That the Local Government Finance (Scotland) O...              1   
2  That the Local Government Finance (Scotland) O...              1   
3  That the Local Government Finance (Scotland) O...              1   
4  That the Local Government Finance (Scotland) O...              1   

   govt_opp_motion motion_party_affiliation  \
0                1                      Lab   
1                1                      Lab   
2                1                      Lab   
3                1                      Lab   
4                1                      Lab   

                                                utt1  \
0  I trust that the House will not feel that ther...   
1  The Secretary State talks of the lack of fuss ...   
2  May I assure the right hon. Gentleman that he ...   
3  Is the hon. Gentleman aware that, ever since t...   
4  The hon. Gentleman will notice that the Childr...   

                                                utt2  \
0  If one considers the argument from a religious...   
1  The right hon. Gentleman may not have heard fu...   
2  Will the hon. Gentleman clarify what he meant ...   
3  I rise as one who, in the past, has not been a...   
4  I thank the hon. Gentleman for his generosity ...   

                                                utt3  \
0  I accept that we shall all face death at one t...   
1                                     North Tayside.   
2                                                NaN   
3  It would be inappropriate to allow the debate ...   
4                                                NaN   

                                                utt4  \
0  When we listen to my hon. Friend's case, we mu...   
1    The Secretary of State's geography is terrible.   
2                                                NaN   
3  Why are the problems of so many of our people,...   
4                                                NaN   

                                                utt5  manual_speech  \
0  I do not think that we want that sort of socie...              0   
1  Would not the £40 million gap in the assumptio...              0   
2                                                NaN              1   
3  Today's debate is the first of this sort under...              0   
4                                                NaN              1   

   vote_speech party_affiliation            name  rebellion  
0            0               Lab  Kevin McNamara        3.2  
1            0               SNP    John Swinney        0.4  
2            1               Lab   John McAllion        4.5  
3            1               Lab    Ian Davidson        3.1  
4            1               Lab      Maria Fyfe        2.3

In [4]:
data.describe()

id  manual_motion  govt_opp_motion  manual_speech  \
count  1251.000000    1251.000000      1251.000000    1251.000000   
mean     76.455635       0.396483         0.414868       0.564349   
std      33.891100       0.489362         0.492896       0.496040   
min       1.000000       0.000000         0.000000       0.000000   
25%      50.000000       0.000000         0.000000       0.000000   
50%      80.000000       0.000000         0.000000       1.000000   
75%     105.000000       1.000000         1.000000       1.000000   
max     129.000000       1.000000         1.000000       1.000000   

       vote_speech    rebellion  
count  1251.000000  1251.000000  
mean      0.569944     1.173141  
std       0.495282     1.944312  
min       0.000000     0.000000  
25%       0.000000     0.200000  
50%       1.000000     0.600000  
75%       1.000000     1.400000  
max       1.000000    25.100000

In [5]:
new_data=data[['id','manual_motion', 'utt1','utt2','utt3','utt4','utt5','govt_opp_motion','manual_speech','vote_speech','party_affiliation','motion_party_affiliation']]

In [6]:
new_data.describe()

id  manual_motion  govt_opp_motion  manual_speech  vote_speech
count  1251.000000    1251.000000      1251.000000    1251.000000  1251.000000
mean     76.455635       0.396483         0.414868       0.564349     0.569944
std      33.891100       0.489362         0.492896       0.496040     0.495282
min       1.000000       0.000000         0.000000       0.000000     0.000000
25%      50.000000       0.000000         0.000000       0.000000     0.000000
50%      80.000000       0.000000         0.000000       1.000000     1.000000
75%     105.000000       1.000000         1.000000       1.000000     1.000000
max     129.000000       1.000000         1.000000       1.000000     1.000000

# Combining all utterances for analysis

In [7]:
new_data["utt2"].fillna(" ", inplace=True)
new_data["utt3"].fillna(" ", inplace=True)
new_data["utt4"].fillna(" ", inplace=True)
new_data["utt5"].fillna(" ", inplace=True)

/home/adityaasinha28/anaconda3/lib/python3.6/site-packages/pandas/core/generic.py:4355: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(new_data)


In [8]:
new_data

id  manual_motion                                               utt1  \
0       1              1  I trust that the House will not feel that ther...   
1       2              1  The Secretary State talks of the lack of fuss ...   
2       2              1  May I assure the right hon. Gentleman that he ...   
3       2              1  Is the hon. Gentleman aware that, ever since t...   
4       2              1  The hon. Gentleman will notice that the Childr...   
5       3              0  Does my hon. Friend agree that, whereas last w...   
6       3              0  Does my hon. Friend agree that part of the dis...   
7       3              0  First, I must declare an interest as the chair...   
8       4              1  My hon. Friend mentions Staffordshire and the ...   
9       4              1  My right hon. Friend probably heard the interv...   
10      4              1  Does my right hon. Friend agree that the issue...   
11      4              1  The Minister will be aware that the Gloucester...   
12      5              1  I welcome what my right hon. Friend has done, ...   
13      5              1  Is the right hon. Gentleman aware of the publi...   
14      5              1  I am grateful to the Secretary of State for gi...   
15      5              1  On the point about local communities supportin...   
16      5              1  Barnsley council has this year received its hi...   
17      5              1  Having insulted everybody north of Watford by ...   
18      5              1  Does my right hon. Friend agree that local aut...   
19      5              1  Surely, given the fact that the head count is ...   
20      5              1  Is the hon. Gentleman aware that, including th...   
21      5              1  It is with some reluctance that I join this de...   
22      5              1  I thank the hon. Gentleman for giving way. I a...   
23      6              1  Is the hon. Gentleman aware that, through COSL...   
24      6              1       Did I hear the hon. Gentleman refer to CCTV?   
25      7              0  I am glad that the regulations have come befor...   
26      8              1  I shall not delay the House for long in giving...   
27      8              1  Perhaps I may assist the hon. Member for North...   
28      9              1  Would the hon. Gentleman confirm that one of t...   
29      9              1  Does my hon. Friend agree that, whatever the a...   
...   ...            ...                                                ...   
1221  127              0  I have done work in my local area of Tyneside ...   
1222  127              0  I am interested to hear the hon. Lady refer to...   
1223  127              0  Does my hon. Friend agree that, if we are goin...   
1224  127              0  I represent the constituency in which Wrexham ...   
1225  127              0  I am grateful to you, Mr Speaker, for giving m...   
1226  127              0  Helping prisoners to maintain stable family re...   
1227  127              0  I not only join others in celebrating the cond...   
1228  128              0  Does my hon. Friend agree that Members on both...   
1229  128              0  I am sure my hon. Friend will be aware that se...   
1230  128              0  Before I entered the House, I sat on the board...   
1231  128              0  Not everything that the hon. Lady is saying is...   
1232  128              0  In the Corbyn land of rhetoric, the hon. Lady ...   
1233  128              0  Despite all the howling we have just heard fro...   
1234  128              0  It was a delight to hear the maiden speech of ...   
1235  128              0  I, too, congratulate the hon. Member for Oldha...   
1236  128              0  One minute will be just enough to pay tribute ...   
1237  128              0  My hon. Friend is making an excellent point. W...   
1238  129              0  A great deal of private sector industrial inve...   
1239  129              0  One of the levers at the dispos

In [9]:
for i in new_data.index:
    #speech = new_data.at[i,'utt1']
    #processed_speech = preprocess_tweet(speech)
    new_data.at[i, 'utt1'] = new_data.at[i, 'utt1'] + " " + new_data.at[i, 'utt2'] +" " + new_data.at[i, 'utt3'] + " " +new_data.at[i, 'utt4'] + " " +new_data.at[i, 'utt5']    
    
   

In [10]:
new_data['utt1'][0]

'I trust that the House will not feel that there is a lack of compassion on any side of the argument about such a dreadful and painful subject. Many of us have had experiences similar to that of my hon. Friend the Member for Bassetlaw, either directly in our own families or on the periphery of decisions to turn off life-sustaining machines. Therefore, no one should be seen as lacking compassion. I find it strange that, having explained the present position in law, my hon. Friend suggested that legislation was required. Even in the case that he cited, the House of Lords has made the position quite clear. If a doctor administers medicine to alleviate pain and suffering and that results in the shortening of a person\'s life—although that does not necessarily happen—it is not euthanasia or murder. Much depends on the intent of the person administering the medicine. If one considers the argument from a religious point of view, different people will have different attitudes. I understand tha

In [11]:
new_data=new_data[['id','manual_motion', 'utt1','govt_opp_motion','manual_speech','vote_speech','party_affiliation','motion_party_affiliation']]

In [12]:
def preprocess_speech(speech):
    processed_speech = []
    # Convert to lower case
    speech = speech.lower()
    # Replaces URLs with the word URL
    speech = re.sub(r'((www\.[\S]+)|(https?://[\S]+))', ' URL ', speech)
    # Replace @handle with the word USER_MENTION
    speech = re.sub(r'@[\S]+', 'USER_MENTION', speech)
    # Replaces #hashtag with hashtag
    speech = re.sub(r'#(\S+)', r' \1 ', speech)
    # Remove RT (respeech)
    speech = re.sub(r'\brt\b', '', speech)
    # Replace 2+ dots with space
    speech = re.sub(r'\.{2,}', ' ', speech)
    # Strip space, " and ' from speech
    speech = speech.strip(' "\'')
    # Replace emojis with either EMO_POS or EMO_NEG
    #speech = handle_emojis(speech)
    # Replace multiple spaces with a single space
    speech = re.sub(r'\s+', ' ', speech)
    words = speech.split()
    
    #f=open("stopwords.txt", 'r')
    #wordn=f.read()
    #stopwords = nltk.corpus.stopwords.words('english')
    #stopwords += re.split('; |, |\*|\n',wordn)
    
    hansard_stopwords = ({'friend', 'honourable', 'hon', 'gentleman', 'lady','give', 'way', 'house', 'amendment', 'beg', 'move','member', 'question', 'green', 'white', 'paper', 'bill', 'statement', 'government', 'prime', 'minister','opposition', 'party', 'mr', 'rose'})
    sklhansard_stopwords = text.ENGLISH_STOP_WORDS.union(hansard_stopwords)
    
    
    f= open("stopwords.txt","r+")
    txt=f.read()
    result = [x.strip() for x in txt.split(',')]
    word =  set(result)
    sklhansard_stopwords= sklhansard_stopwords.union(word)
    
    for word in words:
        word = preprocess_word(word)
        if is_valid_word(word):
            if word not in sklhansard_stopwords:
                   processed_speech.append(word)
                    
    print(sklhansard_stopwords)
    
    

    for word in words:
        word = preprocess_word(word)
        if is_valid_word(word):
            if word not in sklhansard_stopwords:
               	processed_speech.append(word)

    return ' '.join(processed_speech)

In [13]:
def preprocess_word(word):
    # Remove punctuation
    word = word.strip('\'"?!,.():;')
    # Convert more than 2 letter repetitions to 2 letter
    # funnnnny --> funny
    word = re.sub(r'(.)\1+', r'\1\1', word)
    # Remove - & '
    word = re.sub(r'(-|\')', '', word)
    return word


In [14]:
def is_valid_word(word):
    # Check if word begins with an alphabet
    return (re.search(r'^[a-zA-Z][a-z0-9A-Z\._]*$', word) is not None)

In [15]:
for i in new_data.index:
    speech = new_data.at[i,'utt1']
    processed_speech = preprocess_speech(speech)
    new_data.at[i, 'utt1'] = processed_speech

frozenset({'', 'bann', 'chelsea', 'reynolds', 'liam', 'maidstone', 'putney', 'hastings', 'rudd', 'christopher', 'port', 'third', 'jenkin', 'dagenham', 'meriden', 'adams', 'edinburgh', 'after', 'onto', 'harriet', 'durkan', 'linlithgow', 'shaun', 'white', 'outwood', 'roy', 'dennis', 'gale', 'diana', 'northwood', 'barwell', 'batley', 'view', 'raynsford', 'ian', 'thus', 'karen', 'dearne', 'esher', 'lansley', 'spelthorne', 'worthing', 'than', 'urmston', 'hemsworth', 'william', 'deeside', 'isleworth', 'argyll', 'always', 'fitzpatrick', 'simon', 'leeds', 'washington', 'parish', 'arran', 'wakefield', 'benyon', 'bromley', 'denis', 'goldsmith', 'scott', 'rowley', 'there', 'darwen', 'douglas', 'gilmore', 'that', 'paul', 'therese', 'clarke', 'drax', 'danny', 'tobias', 'afriyie', 'wrekin', 'could', 'jim', 'barrow', 'call', 'goole', 'aldridgerownhills', 'falmouth', 'finchley', 'dumfries', 'hall', 'committee', 'banff', 'royton', 'show', 'angie', 'moray', 'dinefwr', 'further', 'mcguinness', 'grahame',

frozenset({'', 'bann', 'chelsea', 'reynolds', 'liam', 'maidstone', 'putney', 'hastings', 'rudd', 'christopher', 'port', 'third', 'jenkin', 'dagenham', 'meriden', 'adams', 'edinburgh', 'after', 'onto', 'harriet', 'durkan', 'linlithgow', 'shaun', 'white', 'outwood', 'roy', 'dennis', 'gale', 'diana', 'northwood', 'barwell', 'batley', 'view', 'raynsford', 'ian', 'thus', 'karen', 'dearne', 'esher', 'lansley', 'spelthorne', 'worthing', 'than', 'urmston', 'hemsworth', 'william', 'deeside', 'isleworth', 'argyll', 'always', 'fitzpatrick', 'simon', 'leeds', 'washington', 'parish', 'arran', 'wakefield', 'benyon', 'bromley', 'denis', 'goldsmith', 'scott', 'rowley', 'there', 'darwen', 'douglas', 'gilmore', 'that', 'paul', 'therese', 'clarke', 'drax', 'danny', 'tobias', 'afriyie', 'wrekin', 'could', 'jim', 'barrow', 'call', 'goole', 'aldridgerownhills', 'falmouth', 'finchley', 'dumfries', 'hall', 'committee', 'banff', 'royton', 'show', 'angie', 'moray', 'dinefwr', 'further', 'mcguinness', 'grahame',

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



frozenset({'', 'bann', 'chelsea', 'reynolds', 'liam', 'maidstone', 'putney', 'hastings', 'rudd', 'christopher', 'port', 'third', 'jenkin', 'dagenham', 'meriden', 'adams', 'edinburgh', 'after', 'onto', 'harriet', 'durkan', 'linlithgow', 'shaun', 'white', 'outwood', 'roy', 'dennis', 'gale', 'diana', 'northwood', 'barwell', 'batley', 'view', 'raynsford', 'ian', 'thus', 'karen', 'dearne', 'esher', 'lansley', 'spelthorne', 'worthing', 'than', 'urmston', 'hemsworth', 'william', 'deeside', 'isleworth', 'argyll', 'always', 'fitzpatrick', 'simon', 'leeds', 'washington', 'parish', 'arran', 'wakefield', 'benyon', 'bromley', 'denis', 'goldsmith', 'scott', 'rowley', 'there', 'darwen', 'douglas', 'gilmore', 'that', 'paul', 'therese', 'clarke', 'drax', 'danny', 'tobias', 'afriyie', 'wrekin', 'could', 'jim', 'barrow', 'call', 'goole', 'aldridgerownhills', 'falmouth', 'finchley', 'dumfries', 'hall', 'committee', 'banff', 'royton', 'show', 'angie', 'moray', 'dinefwr', 'further', 'mcguinness', 'grahame',

frozenset({'', 'bann', 'chelsea', 'reynolds', 'liam', 'maidstone', 'putney', 'hastings', 'rudd', 'christopher', 'port', 'third', 'jenkin', 'dagenham', 'meriden', 'adams', 'edinburgh', 'after', 'onto', 'harriet', 'durkan', 'linlithgow', 'shaun', 'white', 'outwood', 'roy', 'dennis', 'gale', 'diana', 'northwood', 'barwell', 'batley', 'view', 'raynsford', 'ian', 'thus', 'karen', 'dearne', 'esher', 'lansley', 'spelthorne', 'worthing', 'than', 'urmston', 'hemsworth', 'william', 'deeside', 'isleworth', 'argyll', 'always', 'fitzpatrick', 'simon', 'leeds', 'washington', 'parish', 'arran', 'wakefield', 'benyon', 'bromley', 'denis', 'goldsmith', 'scott', 'rowley', 'there', 'darwen', 'douglas', 'gilmore', 'that', 'paul', 'therese', 'clarke', 'drax', 'danny', 'tobias', 'afriyie', 'wrekin', 'could', 'jim', 'barrow', 'call', 'goole', 'aldridgerownhills', 'falmouth', 'finchley', 'dumfries', 'hall', 'committee', 'banff', 'royton', 'show', 'angie', 'moray', 'dinefwr', 'further', 'mcguinness', 'grahame',

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
max_features = 20000
tokenizer = Tokenizer(num_words=max_features, split=' ')
tokenizer.fit_on_texts(new_data['utt1'].values)
X = tokenizer.texts_to_sequences(new_data['utt1'].values)
X = pad_sequences(X)

In [17]:
from sklearn.feature_extraction.text import TfidfVectorizer
hansard_stopwords = ({'friend', 'honourable', 'hon', 'gentleman', 'lady','give', 'way', 'house', 'amendment', 'beg', 'move','member', 'question', 'green', 'white', 'paper', 'bill', 'statement', 'government', 'prime', 'minister','opposition', 'party', 'mr', 'rose'})
sklhansard_stopwords = text.ENGLISH_STOP_WORDS.union(hansard_stopwords)
vectorizer = TfidfVectorizer(min_df=5, max_df = 1.0, 
ngram_range=(1,3), sublinear_tf=True, use_idf =True, 
stop_words=sklhansard_stopwords)

In [18]:
val=new_data['utt1']
val

0       trust feel lack compassion argument dreadful p...
1       secretary state talks lack fuss local settleme...
2       assure right probably thinking sad matters lon...
3       aware beginning urban aid programme projects l...
4       notice children scotland act enacted operation...
5       does agree week treated pan economics case tin...
6       does agree disaster governments plans announce...
7       declare chairman investment management busines...
8       mentions northern relief road police authority...
9       right probably heard intervention described ce...
10      does right agree issue just numbers abandonmen...
11      aware gloucestershire police lowest increase c...
12      welcome right aware representations metropolit...
13      right aware public claim ruth coleman leader w...
14      grateful secretary state giving impressed rema...
15      local communities supporting council tax level...
16      council year received highest settlement fifth...
17      having

In [19]:
Y=new_data['manual_speech']
Y

0       0
1       0
2       1
3       0
4       1
5       1
6       1
7       1
8       0
9       0
10      0
11      0
12      1
13      0
14      0
15      1
16      1
17      1
18      0
19      0
20      1
21      0
22      1
23      1
24      1
25      1
26      1
27      1
28      0
29      1
       ..
1221    1
1222    1
1223    1
1224    1
1225    0
1226    0
1227    0
1228    1
1229    1
1230    0
1231    0
1232    0
1233    0
1234    1
1235    0
1236    1
1237    1
1238    1
1239    0
1240    0
1241    1
1242    1
1243    1
1244    1
1245    1
1246    0
1247    1
1248    1
1249    1
1250    0
Name: manual_speech, Length: 1251, dtype: int64

In [20]:
val_train=vectorizer.fit_transform(val.tolist())
val_train

<1251x2950 sparse matrix of type '<class 'numpy.float64'>'
	with 55217 stored elements in Compressed Sparse Row format>

# Using a TF-IDF Vectorizer and Transformer 

In [21]:
from sklearn.feature_extraction.text import TfidfTransformer
transformer = TfidfTransformer(use_idf=True, smooth_idf=True, sublinear_tf=False)
# speeches_train_corpus = transformer.fit_transform(speeches_train_corpus)
# speeches_test_corpus = transformer.transform(speeches_test_corpus)
val_train = transformer.fit_transform(val_train)

In [22]:
val_train.shape

(1251, 2950)

In [23]:
from sklearn.preprocessing import LabelEncoder

lb_make = LabelEncoder()
new_data["party_code"] = lb_make.fit_transform(new_data["party_affiliation"])
new_data

lb_mp = LabelEncoder()
new_data["motion_party_code"] = lb_mp.fit_transform(new_data["motion_party_affiliation"])
new_data



/home/adityaasinha28/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.
/home/adityaasinha28/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


id  manual_motion                                               utt1  \
0       1              1  trust feel lack compassion argument dreadful p...   
1       2              1  secretary state talks lack fuss local settleme...   
2       2              1  assure right probably thinking sad matters lon...   
3       2              1  aware beginning urban aid programme projects l...   
4       2              1  notice children scotland act enacted operation...   
5       3              0  does agree week treated pan economics case tin...   
6       3              0  does agree disaster governments plans announce...   
7       3              0  declare chairman investment management busines...   
8       4              1  mentions northern relief road police authority...   
9       4              1  right probably heard intervention described ce...   
10      4              1  does right agree issue just numbers abandonmen...   
11      4              1  aware gloucestershire police lowest increase c...   
12      5              1  welcome right aware representations metropolit...   
13      5              1  right aware public claim ruth coleman leader w...   
14      5              1  grateful secretary state giving impressed rema...   
15      5              1  local communities supporting council tax level...   
16      5              1  council year received highest settlement fifth...   
17      5              1  having insulted everybody using expression quo...   
18      5              1  does right agree local authority leaders parti...   
19      5              1  surely given fact head count months date local...   
20      5              1  aware including increase ssa services cent set...   
21      5              1  reluctance join debate essentially debate good...   
22      5              1  thank giving sure premature welcome bench case...   
23      6              1  aware cosla local authorities agreed prioritie...   
24      6              1  did hear refer cctv welcome parliament july el...   
25      7              0  glad regulations come tonight gives opportunit...   
26      8              1  shall delay giving oppositions resolution appr...   
27      8              1  assist understand representations behalf firm ...   
28      9              1  confirm representations received behalf rural ...   
29      9              1  does agree arguments figures ultimate public f...   
...   ...            ...                                                ...   
1221  127              0  work local area veterans group suffering postt...   
1222  127              0  interested hear refer substance abuse know fig...   
1223  127              0  does agree going reduce strain prisons essenti...   
1224  127              0  represent prison built does welcome fact priso...   
1225  127              0  grateful speaker giving opportunity speak impo...   
1226  127              0  helping prisoners maintain stable family relat...   
1227  127              0  join celebrating conduct debate commend choice...   
1228  128              0  does agree sides fed excuse excuse broken prom...   
1229  128              0  sure aware senior citizens business working ch...   
1230  128              0  entered sat board nonexecutive director bus aw...   
1231  128              0  saying incorrect obviously position bus servic...   
1232  128              0  land rhetoric forgotten fares went year frozen...   
1233  128              0  despite howling just heard oil prices wanted f...   
1234  128              0  delight hear maiden speech insightful contribu...   
1235  128              0  congratulate wish securing metrolink extension...   
1236  128              0  minute just pay tribute like thank brilliant m...   
1237  128              0  making excellent comment introduction fare inc...   
1238  129              0  deal private sector industrial investment past...   
1239  129              0  levers disposal increase export

In [25]:
#num_data=new_data[['manual_motion','govt_opp_motion','vote_speech','id']]
num_data=new_data[['govt_opp_motion','id','manual_motion','party_code','motion_party_code']]
num_data

govt_opp_motion   id  manual_motion  party_code  motion_party_code
0                   1    1              1           8                  3
1                   1    2              1          11                  3
2                   1    2              1           8                  3
3                   1    2              1           8                  3
4                   1    2              1           8                  3
5                   0    3              0           0                  0
6                   0    3              0           0                  0
7                   0    3              0           0                  0
8                   1    4              1           8                  3
9                   1    4              1           0                  3
10                  1    4              1           0                  3
11                  1    4              1           0                  3
12                  1    5              1           8                  3
13                  1    5              1           0                  3
14                  1    5              1           7                  3
15                  1    5              1           8                  3
16                  1    5              1           8                  3
17                  1    5              1           8                  3
18                  1    5              1           0                  3
19                  1    5              1           7                  3
20                  1    5              1           8                  3
21                  1    5              1           8                  3
22                  1    5              1           8                  3
23                  1    6              1           8                  3
24                  1    6              1           8                  3
25                  0    7              0           7                  0
26                  1    8              1           0                  3
27                  1    8              1           8                  3
28                  1    9              1           0                  3
29                  1    9              1           8                  3
...               ...  ...            ...         ...                ...
1221                0  127              0           8                  3
1222                0  127              0           1                  3
1223                0  127              0           0                  3
1224                0  127              0           8                  3
1225                0  127              0           0                  3
1226                0  127              0           0                  3
1227                0  127              0           0                  3
1228                0  128              0           8                  3
1229                0  128              0           8                  3
1230                0  128              0           0                  3
1231                0  128              0           0                  3
1232                0  128              0           0                  3
1233                0  128              0           0                  3
1234                0  128              0           4                  3
1235                0  128              0           0                  3
1236                0  128              0           8                  3
1237                0  128              0           8                  3
1238                0  129              0          11                  4
1239                0  129              0           0                  4
1240                0  129              0           0                  4
1241                0  129              0           8                  4
1242                0  129              0           8                  4
1243                0  129              0           0           

# Combining metadata with the text for prediction 
 "Manual_Speech" is predicted by training on "text", "govt_opp_motion", "id",	"manual_motion",	"party_code",	"vote_speech" and "motion_party_code"

In [26]:
from scipy.sparse import hstack as hs
from numpy import hstack

In [27]:
new_train_data=hs([val_train,num_data])

In [28]:
def create_GRU(X_train_rec):
    embed_dim = 128
    lstm_out = 196
    max_features=200

    from keras.layers import LSTM, Convolution1D, Flatten, Dropout, Dense, GRU

    
    model = Sequential()

    model.add(Embedding(200, embed_dim,input_length = X_train_rec.shape[1]))
    model.add(GRU(units=16, name = "gru_1",return_sequences=True))
    model.add(GRU(units=8, name = "gru_2" ,return_sequences=True))
    model.add(GRU(units=4, name= "gru_3"))
    model.add(Dense(1, activation='sigmoid',name="dense_1"))
    
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    
    return model

In [35]:
import pandas
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Embedding, LSTM, SpatialDropout1D
from sklearn.model_selection import train_test_split
from keras.utils.np_utils import to_categorical
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from keras.layers import Dense, Dropout, Activation , GRU
from keras.layers import Embedding, Flatten
from keras.layers import Conv1D, GlobalMaxPooling1D, Bidirectional
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras.layers import LSTM, Convolution1D, Flatten, Dropout, Dense


folds_no = 10
kf = StratifiedKFold(n_splits=folds_no, shuffle=True)

In [36]:
num_data_arr=np.array(num_data)
num_data.iloc[[1,2]]

govt_opp_motion  id  manual_motion  party_code  motion_party_code
1                1   2              1          11                  3
2                1   2              1           8                  3

## Running the GRU model with 10-fold cross validation 

In [32]:

cvscores = []
X_sparse=new_train_data.todense()
for train_index, test_index in kf.split(val,Y):
    
    
    X_train, X_test = val[train_index], val[test_index]
    y_train, y_test = Y[train_index], Y[test_index]
    num_data_train, num_data_test = num_data.iloc[train_index],num_data.iloc[test_index]
    X_val_train=vectorizer.fit_transform(X_train.tolist())
    X_val_test=vectorizer.transform(X_test.tolist())
    

    transformer = TfidfTransformer(use_idf=True, smooth_idf=True, sublinear_tf=False)
    X_val_train = transformer.fit_transform(X_val_train)
    X_val_test=transformer.transform(X_val_test)
    X_new_train_data=hs([X_val_train,num_data_train])
    X_new_test_data=hs([X_val_test,num_data_test])    
    embed_dim = 128
    lstm_out = 196
    max_features=200

    model = Sequential()
    
    model.add(Embedding(200, 128,input_length = (X_new_train_data.toarray()).shape[1]))
    model.add(GRU(units=16, name = "gru_1",return_sequences=True))
    model.add(GRU(units=8, name = "gru_2" ,return_sequences=True))
    model.add(GRU(units=4, name= "gru_3"))
    model.add(Dense(1, activation='sigmoid',name="dense_1"))
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    
    
    
    model.fit(X_new_train_data.toarray(), y_train, epochs=10, batch_size=32, verbose=1)
    scores = model.evaluate(X_new_test_data.toarray(), y_test, verbose=1)
    print("%s: %.2f%%" % (model.metrics_names[1], scores[1]*100))
    
    print("Values are" ,model.metrics_names, scores)
    cvscores.append(scores[1] * 100)
print("%.2f%% (+/- %.2f%%)" % (np.mean(cvscores), np.std(cvscores)))



Epoch 1/10
625/625 [==============================] - 32s 51ms/step - loss: 0.6753 - acc: 0.5648
Epoch 2/10
625/625 [==============================] - 29s 46ms/step - loss: 0.6419 - acc: 0.6352
Epoch 3/10
625/625 [==============================] - 30s 47ms/step - loss: 0.5843 - acc: 0.7088
Epoch 4/10
625/625 [==============================] - 29s 47ms/step - loss: 0.5212 - acc: 0.7664
Epoch 5/10
625/625 [==============================] - 30s 48ms/step - loss: 0.4555 - acc: 0.8304
Epoch 6/10
625/625 [==============================] - 30s 47ms/step - loss: 0.4015 - acc: 0.8576
Epoch 7/10
625/625 [==============================] - 29s 47ms/step - loss: 0.3807 - acc: 0.8544
Epoch 8/10
625/625 [==============================] - 30s 48ms/step - loss: 0.3409 - acc: 0.9008
Epoch 9/10
625/625 [==============================] - 30s 48ms/step - loss: 0.3217 - acc: 0.9008
Epoch 10/10
626/626 [==============================] - 7s 11ms/step
acc: 82.75%
Values are ['loss', 'acc'] [0.4603513142171378,

In [ ]:
Values are ['loss', 'acc'] [0.19072181322882253, 0.9435483813285828]
91.21% (+/- 2.85%)

(1251, 5)

In [40]:

cvscores = []
X_sparse=new_train_data.todense()
for train_index, test_index in kf.split(val,Y):
    
    
    X_train, X_test = val[train_index], val[test_index]
    y_train, y_test = Y[train_index], Y[test_index]
    num_data_train, num_data_test = num_data.iloc[train_index],num_data.iloc[test_index]
    X_val_train=vectorizer.fit_transform(X_train.tolist())
    X_val_test=vectorizer.transform(X_test.tolist())
    

    transformer = TfidfTransformer(use_idf=True, smooth_idf=True, sublinear_tf=False)
    X_val_train = transformer.fit_transform(X_val_train)
    X_val_test=transformer.transform(X_val_test)
    X_new_train_data=hs([X_val_train,num_data_train])
    X_new_test_data=hs([X_val_test,num_data_test])    
    embed_dim = 128
    lstm_out = 196
    max_features=20000

    model = Sequential()
    
    model.add(Embedding(4000, 128,input_length = (X_new_train_data.toarray()).shape[1]))
    #model.add(GRU(units=16, name = "gru_1",return_sequences=True))
    #model.add(GRU(units=8, name = "gru_2" ,return_sequences=True))
    #model.add(GRU(units=4, name= "gru_3"))
    #model.add(Dense(1, activation='sigmoid',name="dense_1"))
    
    model.add(Dropout(0.2))

    model.add(Conv1D(64,kernel_size=3,padding='same',activation='relu',strides=1))
    model.add(GlobalMaxPooling1D())

    model.add(Dense(128,activation='relu'))
    model.add(Dropout(0.2))
    model.add(Dense(1, activation='sigmoid',name="dense_1"))
    
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    
    
    
    model.fit(X_new_train_data.toarray(), y_train, epochs=10, batch_size=64, verbose=1)
    scores = model.evaluate(X_new_test_data.toarray(), y_test, verbose=1)
    print("%s: %.2f%%" % (model.metrics_names[1], scores[1]*100))
    
    print("Values are" ,model.metrics_names, scores)
    cvscores.append(scores[1] * 100)
print("%.2f%% (+/- %.2f%%)" % (np.mean(cvscores), np.std(cvscores)))



Epoch 1/10
1125/1125 [==============================] - 19s 17ms/step - loss: 0.6782 - acc: 0.5449
Epoch 2/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.5995 - acc: 0.6747
Epoch 3/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.4829 - acc: 0.7449
Epoch 4/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.3943 - acc: 0.8284
Epoch 5/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.3207 - acc: 0.8702
Epoch 6/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.2841 - acc: 0.8853
Epoch 7/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.2487 - acc: 0.8960
Epoch 8/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.2217 - acc: 0.9120
Epoch 9/10
1125/1125 [==============================] - 18s 16ms/step - loss: 0.2039 - acc: 0.9076
Epoch 10/10
126/126 [==============================] - 1s 5ms/step
acc: 87.30%
Values are ['loss', 'acc'] [0.

1127/1127 [==============================] - 22s 20ms/step - loss: 0.3582 - acc: 0.8438
Epoch 5/10
1127/1127 [==============================] - 22s 19ms/step - loss: 0.3094 - acc: 0.8687
Epoch 6/10
1127/1127 [==============================] - 21s 18ms/step - loss: 0.2898 - acc: 0.8731
Epoch 7/10
1127/1127 [==============================] - 22s 19ms/step - loss: 0.2627 - acc: 0.8855
Epoch 8/10
1127/1127 [==============================] - 21s 18ms/step - loss: 0.2397 - acc: 0.8980
Epoch 9/10
1127/1127 [==============================] - 23s 21ms/step - loss: 0.2243 - acc: 0.9024
Epoch 10/10
124/124 [==============================] - 1s 7ms/step
acc: 91.94%
Values are ['loss', 'acc'] [0.2195283890731873, 0.919354832941486]
Epoch 1/10
1127/1127 [==============================] - 22s 20ms/step - loss: 0.6775 - acc: 0.5617
Epoch 2/10
1127/1127 [==============================] - 23s 21ms/step - loss: 0.6146 - acc: 0.6584
Epoch 3/10
1127/1127 [==============================] - 25s 22ms/step - l